## TRABALHO 2

### Ana Luiza Figueiredo Gouvea

#### Refazer os exercícios de MapReduce, dessa vez com Spark RDD. 

In [1]:
#Instalação das bibliotecas:
!pip install pyspark
!pip install jupyter
!pip install findspark

In [2]:
#Importação da bibiliota
import findspark
import pyspark
import random

findspark.init('C:/Users/analu/anaconda3/Lib/site-packages/pyspark')
#findspark.find()- Erro

In [8]:
#sc = pyspark.SparkContext(appName='trabalho_2')

In [7]:
print(sc)

<SparkContext master=local[*] appName=trabalho_2>


### 1. Utilizando o dataset flights.csv, faça operações MapReduce para calcular

In [9]:
#Importação do arquivo
flights_file = 'file:/Users/analu/Documents/Pos_puc/Big Data/Git/BigDataAulasPUC-20211212T212411Z-001/BigDataAulasPUC/Datasets/Flights_old/flights.csv'
flights_RDD = sc.textFile(flights_file)

In [10]:
# minutos de atraso por aeroporto

def read_line(line):
    record = line.split(',')
    return (record[3],float(record[6]))

delay_RDD = flights_RDD.map(read_line)
print(delay_RDD.reduceByKey(lambda a,b: a+b).take(10))

[('LAX', 149470.0), ('BOS', 49478.0), ('SFO', 124901.0), ('ATL', 261924.0), ('DCA', 27099.0), ('ORD', 274709.0), ('PBI', 26107.0), ('FLL', 63583.0), ('IAD', 54591.0), ('SJU', 12262.0)]


In [11]:
# a) O tempo total de vôo de cada companhia

def temp_total_voo(line):
    record = line.split(',')
    return (record[1], float(record[9]))

temp_total = flights_RDD.map(temp_total_voo).take(500000)
temp_total_RDD = sc.parallelize(temp_total)
temp_total_group_RDD = temp_total_RDD.reduceByKey(lambda a,b: a+b).sortByKey()

for key, values in temp_total_group_RDD.collect():
    print(f'{key} -> {values}')


19393 -> 9959718.0
19690 -> 449242.0
19790 -> 7747256.0
19805 -> 6273366.0
19930 -> 2001295.0
19977 -> 6757883.0
20304 -> 3625141.0
20355 -> 4194811.0
20366 -> 4142864.0
20398 -> 2391168.0
20409 -> 3009096.0
20436 -> 689589.0
20437 -> 799733.0
21171 -> 916098.0


In [23]:
# b) Qual é o destino mais visitado

destinos_visitados = {}

def mais_visitados(linha):
    r = linha.split(',')
    return (r[4], int(1))

destinos_visitados_RDD = flights_RDD.map(mais_visitados)
total_destinos_visitados =destinos_visitados_RDD.reduceByKey(lambda a,b: a+b).take(500000)

for a in total_destinos_visitados:
    destinos_visitados[a[0]] = a[1]

c = int(max(destinos_visitados.values()))
destino_mais_visitado = list(destinos_visitados.keys())[list(destinos_visitados.values()).index(c)]

print(f'{destino_mais_visitado} -> {c}')

ATL -> 30953


In [14]:
# c) Quais aeroportos cada companhia passou

def aeroportos_visitados(line):
    record= line.split(',')
    return (record[1], record[3])

aeroportos = (flights_RDD.map(aeroportos_visitados).take(500000))
aeroportos_RDD = sc.parallelize(aeroportos)

aeroportos_group_RDD = aeroportos_RDD.groupByKey().sortByKey()

for key, values in aeroportos_group_RDD.collect():
    print(key, set(values))
    print('\n')

19393 {'MSP', 'OAK', 'HOU', 'CHS', 'ONT', 'ECP', 'FLL', 'MDW', 'SFO', 'PWM', 'MCI', 'RDU', 'CLT', 'RNO', 'LBB', 'ICT', 'SLC', 'OMA', 'PBI', 'SJC', 'BOS', 'SMF', 'SEA', 'SDF', 'JAN', 'LAX', 'ATL', 'IND', 'TPA', 'OKC', 'ISP', 'ORF', 'PIT', 'MHT', 'BHM', 'STL', 'BOI', 'PHL', 'DSM', 'BKG', 'CMH', 'AUS', 'CAK', 'GRR', 'MKE', 'GSP', 'MAF', 'LGA', 'LAS', 'TUL', 'AMA', 'HRL', 'CRP', 'ABQ', 'PNS', 'SAN', 'ELP', 'CLE', 'TUS', 'IAD', 'BUF', 'BDL', 'PHX', 'SNA', 'PVD', 'RIC', 'SAT', 'EYW', 'GEG', 'ROC', 'DAY', 'BNA', 'LIT', 'DAL', 'FNT', 'MSY', 'MCO', 'EWR', 'BWI', 'DTW', 'DCA', 'PDX', 'MEM', 'BUR', 'RSW', 'DEN', 'JAX', 'ALB', 'SJU'}


19690 {'LAX', 'PDX', 'PHX', 'LIH', 'SAN', 'PPG', 'SFO', 'SJC', 'LAS', 'OGG', 'JFK', 'HNL', 'OAK', 'KOA', 'ITO', 'SMF', 'SEA'}


19790 {'COS', 'MSP', 'OAK', 'HOU', 'CHS', 'FLL', 'MDW', 'ECP', 'SFO', 'SYR', 'BZN', 'MSN', 'TRI', 'PWM', 'MCI', 'HNL', 'RDU', 'CLT', 'RNO', 'ICT', 'SLC', 'OMA', 'PBI', 'MDT', 'SJC', 'BOS', 'VPS', 'SMF', 'SEA', 'LIH', 'STT', 'FSD', 'SDF', 'D

In [24]:
# d) O vôo de maior distância de cada companhia

def maior_distancia(line):
    record = line.split(',')
    return (record[1], float(record[10]))

maior_distancia_cia = flights_RDD.map(maior_distancia).take(500000)
maior_distancia_cia_RDD = sc.parallelize(maior_distancia_cia)

maior_distancia_cia_group_RDD = maior_distancia_cia_RDD.groupByKey().sortByKey()

for key, values in maior_distancia_cia_group_RDD.collect():
     print(f'{key} -> {max(set(values))}')

19393 -> 2335.0
19690 -> 4983.0
19790 -> 4502.0
19805 -> 3784.0
19930 -> 2874.0
19977 -> 4962.0
20304 -> 1535.0
20355 -> 2979.0
20366 -> 1389.0
20398 -> 1379.0
20409 -> 2704.0
20436 -> 1703.0
20437 -> 2139.0
21171 -> 2704.0


In [28]:
# e) Qual é o vôo mais frequente de cada companhia

def voo_mais_frequente(line):
    record = line.split(',')
    return (record[1], record[2])

voo_mais_frequente_cia = flights_RDD.map(voo_mais_frequente).take(500000)
voo_mais_frequente_cia_RDD = sc.parallelize(voo_mais_frequente_cia)

voo_mais_frequente_cia_group_RDD =voo_mais_frequente_cia_RDD.groupByKey().sortByKey()

dic_voo_mais_freq = {}
dic_voo_mais_freq_cont = {}

for x in voo_mais_frequente_cia_group_RDD.collect():
    dic_voo_mais_freq[x[0]] = list(x[1])
    
for cia in dic_voo_mais_freq.keys():
    for voo in dic_voo_mais_freq[cia]:
        if voo in dic_voo_mais_freq_cont:
            dic_voo_mais_freq_cont[voo] += 1
        else:
             dic_voo_mais_freq_cont[voo] = 1
            
    mais_frequente = int(max(dic_voo_mais_freq_cont.values()))
    voo_mais_freq= list(dic_voo_mais_freq_cont.keys())[list(dic_voo_mais_freq_cont.values()).index(mais_frequente)]
    dic_voo_mais_freq_cont.clear()
    
    print(f'{cia} -> {mais_frequente} -> {voo_mais_freq}')

19393 -> 170 -> 583
19690 -> 30 -> 1
19790 -> 60 -> 1258
19805 -> 60 -> 29
19930 -> 150 -> 64
19977 -> 75 -> 1246
20304 -> 90 -> 5325
20355 -> 120 -> 409
20366 -> 60 -> 2514
20398 -> 60 -> 2726
20409 -> 59 -> 2054
20436 -> 50 -> 143
20437 -> 46 -> 221
21171 -> 60 -> 251


### 2. Utilizando o dataset shakespeare.txt, faça uma operação de MapReduce para construir um índice invertido contendo como chave uma palavra e como valor uma lista de linhas onde ela foi mencionada.

In [29]:
import string
import nltk
nltk.download('stopwords')
nltk.download('punkt')

shakespeare_file = shakespeare_file = 'file:///Users/analu/Documents/Pos_puc/Big Data/Git/BigDataAulasPUC-20211212T212411Z-001/BigDataAulasPUC/Datasets/shakespeare.txt'
stopwords = nltk.corpus.stopwords.words('english')
punctuation = string.punctuation

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\analu\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\analu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [30]:
def tokenizer(line):
    try:
        # divide por sentencas:
        for s in line.split('\n'):
            # divide por tokens:
            lista_tokens = s.lower().split()
            # No arquivo encontramos o nome da obra @ numero que indica a linha
            numero_linha = lista_tokens.pop(0)
            
            
            # Devido aos erros foi necessário retirar os simbolos do texto           
            simbolos = '!@#$%¨&*()_-+=?/°|\{}~^[],:;>.<£¢¬§ªº°""'
            for i in lista_tokens:
                for simb in simbolos:
                    i = i.replace(simb, '')
                if i not in stopwords and i not in punctuation:
                    yield (i, numero_linha)
    except:
        pass
    
            
    
shakespeare_RDD = sc.textFile(shakespeare_file)
tokens_RDD = shakespeare_RDD.flatMap(tokenizer)
tokens_group_RDD = tokens_RDD.groupByKey().sortByKey(True).collect()


for key, values in tokens_group_RDD:
    print(key, set(values))

''all {'loverscomplaint@7887'}
''among {'loverscomplaint@8194'}
''and {'loverscomplaint@8810'}
''but {'loverscomplaint@10350'}
''gamut' {'tamingoftheshrew@61760'}
''how {'loverscomplaint@10957'}
''lo {'loverscomplaint@9430', 'loverscomplaint@10047'}
''look {'loverscomplaint@8501'}
''my {'loverscomplaint@11254'}
''now {'loverscomplaint@11902'}
''o {'loverscomplaint@9732', 'loverscomplaint@10672'}
''od's {'merrywivesofwindsor@89869'}
''the {'loverscomplaint@9114'}
''tis {'venusandadonis@38936', 'sonnets@52703', 'comedyoferrors@15930', 'venusandadonis@50631', 'allswellthatendswell@28286', 'venusandadonis@45753', 'venusandadonis@24650', 'asyoulikeit@30710'}
''twas {'twogentlemenofverona@82008'}
''when {'loverscomplaint@11565'}
'a {'muchadoaboutnothing@103039', 'readme@371', 'tamingoftheshrew@61817', 'merchantofvenice@100336', '1kinghenryiv@50817', 'muchadoaboutnothing@103092', 'othello@35988', 'kinghenryv@80431', 'othello@36139', 'othello@38148', '3kinghenryvi@22690', 'allswellthatendswell

addition {'troilusandcressida@64350', 'kinglear@50755', 'glossary@506', 'macbeth@46262', 'coriolanus@37294', 'kinghenryv@152744', 'othello@106964', 'coriolanus@37558', 'hamlet@28804', 'troilusandcressida@76272', 'othello@123060', 'sonnets@12587', 'antonyandcleopatra@148397', '1kinghenryiv@47165', 'juliuscaesar@93875', 'allswellthatendswell@88643', 'comedyoferrors@24717', 'hamlet@126095', 'troilusandcressida@119420', 'kinglear@155987', 'othello@101555', 'hamlet@43227', 'kinglear@144139', 'kinglear@92054', 'sonnets@83424', 'muchadoaboutnothing@49302', 'macbeth@9415', 'kingjohn@38876'}
additions {'merrywivesofwindsor@51213', 'loverscomplaint@5056', 'allswellthatendswell@45889', 'kinglear@7044', 'troilusandcressida@8755'}
addle {'romeoandjuliet@67780', 'troilusandcressida@13526', 'troilusandcressida@13542'}
address {'troilusandcressida@156890', 'troilusandcressida@112229', '2kinghenryiv@91792', 'winterstale@80460', 'twelfthnight@12442', '2kinghenryvi@148048', 'midsummersnightsdream@34877',

armoury {'titusandronicus@76916', 'titusandronicus@75307'}
arms {'1kinghenryiv@128165', '2kinghenryvi@131022', 'various@10164', 'troilusandcressida@89160', 'kingrichardiii@62705', '1kinghenryiv@41518', 'kingrichardiii@173612', '1kinghenryiv@128087', 'titusandronicus@1297', 'kinglear@58445', '1kinghenryiv@88540', 'winterstale@103922', 'loveslabourslost@113358', 'kingjohn@108121', 'juliuscaesar@75002', 'kinglear@94283', 'othello@37432', 'rapeoflucrece@76113', 'kingjohn@70721', 'rapeoflucrece@4181', 'hamlet@40145', 'kingrichardii@60918', 'kinghenryviii@105172', 'troilusandcressida@49931', 'kinglear@148419', 'tamingoftheshrew@49612', '2kinghenryvi@146342', '1kinghenryiv@124868', '1kinghenryvi@12692', 'coriolanus@108490', 'rapeoflucrece@77474', 'loveslabourslost@24698', 'kingrichardii@10703', '1kinghenryvi@34691', '1kinghenryvi@80031', 'kingrichardii@17185', 'kingjohn@25756', '1kinghenryvi@41617', 'titusandronicus@71499', 'kingjohn@21348', 'rapeoflucrece@25663', 'titusandronicus@84633', '2k

belated {'glossary@30038'}
belch {'twelfthnight@32596', 'twelfthnight@39941', 'twelfthnight@6450', 'twelfthnight@10634', 'twelfthnight@74545', 'twelfthnight@11576', 'twelfthnight@51421', 'twelfthnight@36770', 'twelfthnight@33499', 'twelfthnight@32828', 'twelfthnight@6359', 'twelfthnight@47941', 'twelfthnight@90151', 'twelfthnight@83129', 'twelfthnight@107619', 'twelfthnight@9580', 'twelfthnight@38901', 'twelfthnight@78400', 'twelfthnight@66467', 'twelfthnight@59162', 'twelfthnight@80613', 'twelfthnight@65569', 'twelfthnight@7934', 'kingrichardiii@41935', 'twelfthnight@82028', 'twelfthnight@7597', 'twelfthnight@40025', 'twelfthnight@258', 'twelfthnight@40142', 'twelfthnight@58623', 'twelfthnight@66961', 'twelfthnight@87592', 'twelfthnight@11462', 'twelfthnight@10443', 'twelfthnight@74253', 'twelfthnight@87286', 'twelfthnight@76006', 'twelfthnight@19089', 'twelfthnight@78315', 'twelfthnight@58997', 'twelfthnight@8926', 'twelfthnight@49881', 'twelfthnight@74962', 'twelfthnight@82410', 'tw

browsed'st {'antonyandcleopatra@22493'}
browsing {'winterstale@64626'}
bruise {'1kinghenryiv@18902', '1kinghenryiv@1634', 'glossary@22841', 'kinghenryv@72791', 'kinglear@148163', 'glossary@37166', 'loveslabourslost@105647', 'muchadoaboutnothing@98669', 'glossary@44961', 'timonofathens@55422', 'measureforemeasure@20384'}
bruised {'othello@24986', 'merrywivesofwindsor@12884', 'comedyoferrors@14567', '1kinghenryiv@143908', 'kinghenryv@130751', 'rapeoflucrece@7798', 'troilusandcressida@149525', 'antonyandcleopatra@126216', 'kingrichardiii@158389', 'kingrichardiii@2696'}
bruises {'2kinghenryiv@94818'}
bruising {'kingrichardiii@165138', '1kinghenryiv@88540', 'coriolanus@71358', 'twogentlemenofverona@12607'}
bruit {'3kinghenryvi@117630', 'glossary@6483', 'timonofathens@105496', 'hamlet@15142', 'troilusandcressida@155764', 'glossary@6455'}
bruited {'macbeth@101086', '1kinghenryvi@43006', '2kinghenryiv@8838'}
brundusium {'antonyandcleopatra@82845'}
brunt {'coriolanus@58536'}
brush {'2kinghenryv

...

reign'd {'sonnets@67688', 'kinghenryviii@26049', 'periclesprinceoftyre@3114', '2kinghenryvi@45339', 'loverscomplaint@8459', '2kinghenryvi@45906', 'kinghenryviii@60586', 'cymbeline@136066', 'kingrichardii@99284'}
reignier {'1kinghenryvi@13898', '1kinghenryvi@6689', '1kinghenryvi@67423', '1kinghenryvi@119556', '1kinghenryvi@128308', '1kinghenryvi@131322', '1kinghenryvi@67161', '1kinghenryvi@110580', '1kinghenryvi@34884', '1kinghenryvi@11928', '1kinghenryvi@119035', '1kinghenryvi@13634', '1kinghenryvi@17768', '1kinghenryvi@35869', '1kinghenryvi@118059', '3kinghenryvi@147781', '1kinghenryvi@119911', '1kinghenryvi@119425', '1kinghenryvi@119829', '1kinghenryvi@68579', '1kinghenryvi@117964', '1kinghenryvi@118800', '1kinghenryvi@120652', '1kinghenryvi@11263', '1kinghenryvi@16714', '1kinghenryvi@11726', '1kinghenryvi@118758', '1kinghenryvi@1184', '1kinghenryvi@31349', '1kinghenryvi@118014', '1kinghenryvi@34427', '1kinghenryvi@118486', '1kinghenryvi@118101', '1kinghenryvi@30866', '1kinghenryvi@1

scann'd {'comedyoferrors@25668', 'hamlet@106506', 'macbeth@59812'}
scant {'glossary@44807', 'merchantofvenice@115019', 'kinglear@66885', 'othello@131301', 'othello@27140', 'kinglear@65163', 'various@16170', 'romeoandjuliet@17527', 'antonyandcleopatra@106949', 'merchantofvenice@66605', 'glossary@44778', 'hamlet@176621'}
scanted {'sonnets@72263', 'kinglear@14089', 'kinglear@79213', 'comedyoferrors@22554', 'merchantofvenice@24780'}
scanter {'hamlet@27082'}
scanting {'kinghenryv@43402'}
scantling {'glossary@44837', 'troilusandcressida@35958'}
scantly {'antonyandcleopatra@73948'}
scants {'troilusandcressida@107491'}
scanty {'glossary@44807'}
scape {'merrywivesofwindsor@87052', 'periclesprinceoftyre@74291', 'romeoandjuliet@66798', '2kinghenryvi@150632', 'romeoandjuliet@107840', 'glossary@44863', 'tamingoftheshrew@50415', 'glossary@44879', 'coriolanus@33623'}
scaped {'othello@137653', 'merrywivesofwindsor@27231', 'tempest@46412'}
scapegraces {'glossary@46891'}
scapes {'othello@21206', 'taming

shrowd {'antonyandcleopatra@98094'}
shrows {'loveslabourslost@87862'}
shrub {'tempest@44356', '3kinghenryvi@78261'}
shrub's {'rapeoflucrece@32162'}
shrubs {'titusandronicus@87214', 'rapeoflucrece@32209', '3kinghenryvi@129171'}
shrug {'coriolanus@34231', 'merchantofvenice@20639', 'winterstale@29244'}
shrug'st {'tempest@21869'}
shrugs {'winterstale@29368'}
shrunk {'rapeoflucrece@66915', 'asyoulikeit@76258', 'romeoandjuliet@109169', 'asyoulikeit@51277', '1kinghenryiv@138763', 'hamlet@19420', 'juliuscaesar@59376', 'timonofathens@46092'}
shudder {'venusandadonis@40223'}
shuddering {'merchantofvenice@66517'}
shudders {'timonofathens@77464'}
shuffle {'merrywivesofwindsor@114397', 'merrywivesofwindsor@38849', 'cymbeline@146431'}
shuffled {'hamlet@78404', 'twelfthnight@67794'}
shuffling {'hamlet@105852', 'hamlet@146532', '1kinghenryiv@77786'}
shun {'cymbeline@127808', 'troilusandcressida@78524', 'measureforemeasure@53296', 'kinglear@82358', 'merchantofvenice@82650', 'periclesprinceoftyre@9015',

sprays {'kinghenryv@64028', '2kinghenryvi@50633', 'kingrichardii@87703'}
spread {'rapeoflucrece@58585', 'kingjohn@14512', 'venusandadonis@50124', 'venusandadonis@27432', 'comedyoferrors@38918', 'periclesprinceoftyre@7189', 'winterstale@26628', '1kinghenryvi@75080', 'sonnets@15464', 'midsummersnightsdream@12856', 'muchadoaboutnothing@48274', 'romeoandjuliet@76455', 'comedyoferrors@27386', '3kinghenryvi@14607', 'hamlet@148359', '1kinghenryvi@25463', 'timonofathens@110452', 'hamlet@114960', '3kinghenryvi@6446', 'loveslabourslost@113784', 'kinghenryviii@50931', 'periclesprinceoftyre@111290', 'romeoandjuliet@8790', 'venusandadonis@41250', '2kinghenryiv@142932', 'kinghenryviii@24899', 'coriolanus@90067', 'kingjohn@101122', '3kinghenryvi@14558', '1kinghenryvi@2813', 'troilusandcressida@35127'}
spreading {'3kinghenryvi@129120', '1kinghenryvi@17228', 'loverscomplaint@3214'}
spreads {'kinglear@109486'}
spright {'venusandadonis@8960', 'rapeoflucrece@8271'}
sprightful {'kingjohn@85993'}
sprightful

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

